In [ ]:
!pip install pyAgrum

In [ ]:
import numpy as np
import pandas as pd
import pyAgrum as gum
import pyAgrum.lib.notebook as gnb

In [ ]:
data = pd.DataFrame(np.array([[0, 0, 109], [0, 1, 127], [1, 0, 150], [1, 1, 314]]),
                   columns=['X', 'Y', 'n'])
print(data)

   X  Y    n
0  0  0  109
1  0  1  127
2  1  0  150
3  1  1  314


Bayesian Network Specification
$P(X)$ and $P(Y|X)$ from data

In [ ]:
bn = gum.BayesNet('bn')
X = bn.add(gum.LabelizedVariable('X','',2))
Y = bn.add(gum.LabelizedVariable('Y','',2))
bn.addArc("X", "Y")
px = data[data['X']==0]['n'].sum()/data['n'].sum()
bn.cpt(X).fillWith([px,1-px])
for x in range(2):
  p = data[(data['X']==x) & (data['Y']==0)]['n'].sum()
  p /= data[data['X']==x]['n'].sum()
  bn.cpt("Y")[{'X': x}] = [p, 1-p]

Showing the BN

In [ ]:
gum.config['notebook','potential_visible_digits']=3
gnb.getBN(bn,size="3!")
gnb.sideBySide(bn.cpt("X"),gnb.getBN(bn,size="1!"),bn.cpt("Y"),captions=['','',''])

Moving from the BN to a SCM (structural causal model) by adding a parent $U$ of $Y$ with four states. The structural equation $Y=f(X,U)$ is such that:
$$Y=\left\{ \begin{array}{ll}0&\mathrm{if}\, U=0\\X&\mathrm{if}\, U=1\\ \neg X&\mathrm{if}\, U=2\\1&\mathrm{if}\, U=3 \end{array}\right.$$

The BN induces constraints on $P(U)$:
$$\sum_{u=0}^3 \delta[f(x,u)-y] \cdot P(u) = P(Y=y|X=x)$$
i.e.,
$$P(U=0) + P(U=1) = P(Y=0|X=0)$$
$$P(U=2) + P(U=3) = P(Y=1|X=0)$$
$$P(U=0) + P(U=2) = P(Y=0|X=1)$$
$$P(U=1) + P(U=3) = P(Y=1|X=1)$$




This corresponds to the following credal set:
$$K(U):=\left\{ P(U)=\left[
  \begin{array}{c} t\\P(Y=0|X=0)-t\\P(Y=0|X=1)-t\\1+t-P(Y=0|X=0)-P(Y=0|X=1)
  \end{array}\right] \quad \forall 0 \leq t \leq \min [P(Y=0|X=0),P(Y=0|X=1)] \right\}$$

  We take 10 values in the given range for $t$ and we check that, for each value, the inferences $P(Y=0|X=0)$ and $P(Y=0|X=1)$ in the SCM are compatible with the BN values.

In [ ]:
p00 = bn.cpt("Y")[{'X': 0}][0]
p01 = bn.cpt("Y")[{'X': 1}][0]
scm=gum.BayesNet('scm')
X=scm.add(gum.LabelizedVariable('X','',2))
Y=scm.add(gum.LabelizedVariable('Y','',2))
U=scm.add(gum.LabelizedVariable('U','',4))
scm.addArc("X", "Y")
scm.addArc("U", "Y")
scm.cpt(X).fillWith([px,1-px])
scm.cpt("Y")[{'X': 0, 'U' : 0}] = [1, 0]
scm.cpt("Y")[{'X': 1, 'U' : 0}] = [1, 0]
scm.cpt("Y")[{'X': 0, 'U' : 1}] = [1, 0]
scm.cpt("Y")[{'X': 1, 'U' : 1}] = [0, 1]
scm.cpt("Y")[{'X': 0, 'U' : 2}] = [0, 1]
scm.cpt("Y")[{'X': 1, 'U' : 2}] = [1, 0]
scm.cpt("Y")[{'X': 0, 'U' : 3}] = [0, 1]
scm.cpt("Y")[{'X': 1, 'U' : 3}] = [0, 1]

ie=gum.LazyPropagation(scm)
for t in np.linspace(0.0,min(p00,p01),10):
  scm.cpt(U).fillWith([t,p00-t,p01-t,1+t-p00-p01])
  ie.setEvidence({'X':0})
  ie.makeInference()
  post1 = ie.posterior("Y")[0]
  ie.setEvidence({'X':1})
  ie.makeInference()
  post2 = ie.posterior("Y")[0]
  print(post1,post2)

0.461864406779661 0.3232758620689655
0.461864406779661 0.3232758620689655
0.461864406779661 0.3232758620689655
0.461864406779661 0.3232758620689655
0.461864406779661 0.3232758620689655
0.46186440677966106 0.3232758620689656
0.46186440677966106 0.3232758620689655
0.461864406779661 0.3232758620689655
0.461864406779661 0.3232758620689655
0.461864406779661 0.3232758620689655


For counterfactual inference, we compute a PNS query. Inferences can be obtained by taking the minimum and the maximum for the extreme points of the credal set, corresponding to the extreme points of the parameter $t$.

In [ ]:
twin=gum.BayesNet('twin')
X=twin.add(gum.LabelizedVariable('X','',2))
Y=twin.add(gum.LabelizedVariable('Y','',2))
X2=twin.add(gum.LabelizedVariable('X2','',2))
Y2=twin.add(gum.LabelizedVariable('Y2','',2))
U=twin.add(gum.LabelizedVariable('U','',4))
twin.addArc("X", "Y")
twin.addArc("U", "Y")
twin.addArc("X2", "Y2")
twin.addArc("U", "Y2")
twin.cpt(X).fillWith([px,1-px])
twin.cpt(X2).fillWith([px,1-px])
twin.cpt("Y")[{'X': 0, 'U' : 0}] = [1, 0]
twin.cpt("Y")[{'X': 1, 'U' : 0}] = [1, 0]
twin.cpt("Y")[{'X': 0, 'U' : 1}] = [1, 0]
twin.cpt("Y")[{'X': 1, 'U' : 1}] = [0, 1]
twin.cpt("Y")[{'X': 0, 'U' : 2}] = [0, 1]
twin.cpt("Y")[{'X': 1, 'U' : 2}] = [1, 0]
twin.cpt("Y")[{'X': 0, 'U' : 3}] = [0, 1]
twin.cpt("Y")[{'X': 1, 'U' : 3}] = [0, 1]
twin.cpt("Y2")[{'X2': 0, 'U' : 0}] = [1, 0]
twin.cpt("Y2")[{'X2': 1, 'U' : 0}] = [1, 0]
twin.cpt("Y2")[{'X2': 0, 'U' : 1}] = [1, 0]
twin.cpt("Y2")[{'X2': 1, 'U' : 1}] = [0, 1]
twin.cpt("Y2")[{'X2': 0, 'U' : 2}] = [0, 1]
twin.cpt("Y2")[{'X2': 1, 'U' : 2}] = [1, 0]
twin.cpt("Y2")[{'X2': 0, 'U' : 3}] = [0, 1]
twin.cpt("Y2")[{'X2': 1, 'U' : 3}] = [0, 1]

# As pyAgrum cannot compute joint queries, we create an auxiliary Boolean variable D that is true iff Y=0 and Y2=1
D=twin.add(gum.LabelizedVariable('D','',2))
twin.addArc("Y", "D")
twin.addArc("Y2", "D")
twin.cpt("D")[{'Y': 0, 'Y2' : 0}] = [1, 0]
twin.cpt("D")[{'Y': 1, 'Y2' : 0}] = [1, 0]
twin.cpt("D")[{'Y': 0, 'Y2' : 1}] = [0, 1]
twin.cpt("D")[{'Y': 1, 'Y2' : 1}] = [1, 0]

ie=gum.LazyPropagation(twin)

pns = []
for t in [0.0,min(p00,p01)]:
  twin.cpt(U).fillWith([t,p00-t,p01-t,1+t-p00-p01])
  ie.setEvidence({'X':0,'X2':1})
  ie.makeInference()
  pns.append(ie.posterior("D")[1])
print(min(pns),"<= PNS <=",max(pns))

0.13858854471069548 <= PNS <= 0.461864406779661


In [ ]:
n_EM_runs = 50

em=gum.BayesNet('em')
X=em.add(gum.LabelizedVariable('X','',2))
Y=em.add(gum.LabelizedVariable('Y','',2))
U=em.add(gum.LabelizedVariable('U','',4))
em.addArc("X", "Y")
em.addArc("U", "Y")
em.cpt(X).fillWith([px,1-px])
em.cpt("Y")[{'X': 0, 'U' : 0}] = [1, 0]
em.cpt("Y")[{'X': 1, 'U' : 0}] = [1, 0]
em.cpt("Y")[{'X': 0, 'U' : 1}] = [1, 0]
em.cpt("Y")[{'X': 1, 'U' : 1}] = [0, 1]
em.cpt("Y")[{'X': 0, 'U' : 2}] = [0, 1]
em.cpt("Y")[{'X': 1, 'U' : 2}] = [1, 0]
em.cpt("Y")[{'X': 0, 'U' : 3}] = [0, 1]
em.cpt("Y")[{'X': 1, 'U' : 3}] = [0, 1]

KU = []

ie2=gum.LazyPropagation(em)
for k in range(n_EM_runs):
  # Random initialisation P(U)
  pU = np.random.rand(4)
  pU /= sum(pU)
  em.cpt(U).fillWith(pU)
  nU = np.zeros(4)
  for t in range(200):
    for x in range(2):
      for y in range(2):
        ie2.setEvidence({'X':x, 'Y':y})
        ie2.makeInference()
        pU = ie2.posterior("U")[:]
        nn = data[(data['X']==x) & (data['Y']==y)]['n'].sum()
        nU += nn*pU
    pU = nU/sum(nU)
    em.cpt(U).fillWith(pU)
  KU.append(pU)

In [ ]:
twin2 = gum.BayesNet('twin')
X=twin2.add(gum.LabelizedVariable('X','',2))
Y=twin2.add(gum.LabelizedVariable('Y','',2))
X2=twin2.add(gum.LabelizedVariable('X2','',2))
Y2=twin2.add(gum.LabelizedVariable('Y2','',2))
U=twin2.add(gum.LabelizedVariable('U','',4))
twin2.addArc("X", "Y")
twin2.addArc("U", "Y")
twin2.addArc("X2", "Y2")
twin2.addArc("U", "Y2")
twin2.cpt(X).fillWith([px,1-px])
twin2.cpt(X2).fillWith([px,1-px])
twin2.cpt("Y")[{'X': 0, 'U' : 0}] = [1, 0]
twin2.cpt("Y")[{'X': 1, 'U' : 0}] = [1, 0]
twin2.cpt("Y")[{'X': 0, 'U' : 1}] = [1, 0]
twin2.cpt("Y")[{'X': 1, 'U' : 1}] = [0, 1]
twin2.cpt("Y")[{'X': 0, 'U' : 2}] = [0, 1]
twin2.cpt("Y")[{'X': 1, 'U' : 2}] = [1, 0]
twin2.cpt("Y")[{'X': 0, 'U' : 3}] = [0, 1]
twin2.cpt("Y")[{'X': 1, 'U' : 3}] = [0, 1]
twin2.cpt("Y2")[{'X2': 0, 'U' : 0}] = [1, 0]
twin2.cpt("Y2")[{'X2': 1, 'U' : 0}] = [1, 0]
twin2.cpt("Y2")[{'X2': 0, 'U' : 1}] = [1, 0]
twin2.cpt("Y2")[{'X2': 1, 'U' : 1}] = [0, 1]
twin2.cpt("Y2")[{'X2': 0, 'U' : 2}] = [0, 1]
twin2.cpt("Y2")[{'X2': 1, 'U' : 2}] = [1, 0]
twin2.cpt("Y2")[{'X2': 0, 'U' : 3}] = [0, 1]
twin2.cpt("Y2")[{'X2': 1, 'U' : 3}] = [0, 1]

# As pyAgrum cannot compute joint queries, we create an auxiliary Boolean variable D that is true iff Y=0 and Y2=1
D=twin2.add(gum.LabelizedVariable('D','',2))
twin2.addArc("Y", "D")
twin2.addArc("Y2", "D")
twin2.cpt("D")[{'Y': 0, 'Y2' : 0}] = [1, 0]
twin2.cpt("D")[{'Y': 1, 'Y2' : 0}] = [1, 0]
twin2.cpt("D")[{'Y': 0, 'Y2' : 1}] = [0, 1]
twin2.cpt("D")[{'Y': 1, 'Y2' : 1}] = [1, 0]

ie3=gum.LazyPropagation(twin2)
pns2 = []

for k in range(n_EM_runs):
  twin2.cpt(U).fillWith(KU[k])
  ie3.setEvidence({'X':0,'X2':1})
  ie3.makeInference()
  pns2.append(ie3.posterior("D")[1])

print(min(pns2),"<= PNS <=",max(pns2))

0.08596601213245787 <= PNS <= 0.5807226753683482
